## 12-Aug-2024 == Air Quality 

#### Tim Spann @PaaSDev

### Milvus - Attu

![milvuslogo](https://milvus.io/images/milvus_logo.svg)


### CODE + COMMUNITY

Please join my meetup group NJ/NYC/Philly/Virtual. 

[https://www.meetup.com/unstructured-data-meetup-new-york/](https://www.meetup.com/unstructured-data-meetup-new-york/)


#### Contact Us

Get Milvused!  [https://milvus.io/](https://milvus.io/)

Read my Newsletter every week! [https://github.com/tspannhw/FLiPStackWeekly/blob/main/142-17June2024.md](https://github.com/tspannhw/FLiPStackWeekly/blob/main/142-17June2024.md)

For more cool Unstructured Data, AI and Vector Database videos check out the Milvus vector database videos here
[https://www.youtube.com/@MilvusVectorDatabase/videos](https://www.youtube.com/@MilvusVectorDatabase/videos)

#### Unstructured Data Meetups 

[https://www.meetup.com/pro/unstructureddata/](https://www.meetup.com/pro/unstructureddata/)
[https://zilliz.com/community/unstructured-data-meetup](https://zilliz.com/community/unstructured-data-meetup)
[https://zilliz.com/event](https://zilliz.com/event)

#### [https://x.com/milvusio](Twitter/X)  

#### [https://www.linkedin.com/company/zilliz/](LinkedIn)

#### [https://discord.com/invite/FjCMmaJng6](Discord)

#### [https://milvusio.medium.com/](Blog)

#### Please star our [https://github.com/milvus-io/milvus](Github)

#### [https://www.youtube.com/@FLaNK-Stack](Youtube)

#### [https://medium.com/@tspann/subscribe](Blog)

In [2]:
import os
from pymilvus import MilvusClient
from dotenv import load_dotenv
load_dotenv(verbose=True)


DIMENSION = 384 
MILVUS_URL = "http://192.168.1.153:19530" 
MILVUS_CLOUD_URL = "https://in05-7bd87b945683c8d.serverless.gcp-us-west1.cloud.zilliz.com" 
COLLECTION_NAME = "airquality"
AQ_URL = "https://www.airnowapi.org/aq/observation/zipCode/current/?format=application/json&distance=5000&zipCode="
AQ_KEY = "&API_KEY="

## do do.env thing
API_KEY = ""

TOKEN = ""

# -----------------------------------------------------------------------------
# Connect to Milvus

# Local Docker Server
milvus_client = MilvusClient( uri=MILVUS_URL )

# Zilliz Cloud
# milvus_client = MilvusClient( uri=MILVUS_URL, token=TOKEN )


In [3]:
import json
import requests
from pymilvus import model
from pymilvus.model.dense import SentenceTransformerEmbeddingFunction

model = SentenceTransformerEmbeddingFunction('all-MiniLM-L6-v2',device='cpu' )



/Users/timothyspann/Downloads/code/milvusvenv/lib/python3.12/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/Users/timothyspann/Downloads/code/milvusvenv/lib/python3.12/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [5]:
from pymilvus import connections
from pymilvus import utility
from pymilvus import FieldSchema, CollectionSchema, DataType, Collection
import pprint

## schema

schema = milvus_client.create_schema(
    enable_dynamic_field=False
)

# Scalar field supports:
#
# BOOL: Boolean (true or false)
# INT8: numpy.int8
# INT16: numpy.int16
# INT32: numpy.int32
# INT64: numpy.int64
# FLOAT: numpy.float32
# DOUBLE: numpy.double
# VARCHAR: VARCHAR
# JSON: JSON

schema.add_field(field_name='id', datatype=DataType.INT64, is_primary=True, auto_id=True)
schema.add_field(field_name='DateObserved', datatype=DataType.VARCHAR, max_length=12)
schema.add_field(field_name="HourObserved", datatype=DataType.INT8)
schema.add_field(field_name="Latitude", datatype=DataType.FLOAT)
schema.add_field(field_name="Longitude", datatype=DataType.FLOAT)
schema.add_field(field_name='ParameterName', datatype=DataType.VARCHAR, max_length=12)
schema.add_field(field_name='ZipCode', datatype=DataType.VARCHAR, max_length=12)
schema.add_field(field_name="AQI", datatype=DataType.INT8)
schema.add_field(field_name="vector", datatype=DataType.FLOAT_VECTOR, dim=DIMENSION)
schema.add_field(field_name="details",  datatype=DataType.VARCHAR, max_length=8000)
schema.add_field(field_name="location",  datatype=DataType.VARCHAR, max_length=2000)

index_params = milvus_client.prepare_index_params()

index_params.add_index(
    field_name="id",
    index_type="STL_SORT"
)

index_params.add_index(
    field_name="vector",
    index_type="IVF_FLAT",
    metric_type="L2",
    params={"nlist": 100}
)

milvus_client.create_collection(
    collection_name = COLLECTION_NAME,
    schema=schema,
    index_params=index_params
)

res = milvus_client.get_load_state(
    collection_name = COLLECTION_NAME
)

print(res)

RPC error: [load_collection], <MilvusException: (code=1100, message=can't change the index for loaded collection: invalid parameter[expected=map[100:451730705225059155 108:451730705225059161]][actual=map[100:451730705225059155 105:451730705225059365 108:451730705225059161]])>, <Time:{'RPC start': '2024-08-12 18:14:52.406004', 'RPC error': '2024-08-12 18:14:52.415976'}>
Failed to load collection: airquality


MilvusException: <MilvusException: (code=1100, message=can't change the index for loaded collection: invalid parameter[expected=map[100:451730705225059155 108:451730705225059161]][actual=map[100:451730705225059155 105:451730705225059365 108:451730705225059161]])>

In [23]:
import numpy

zipcodes = ["08520","94027","02199","11962","94957","90402","94301","07070","90265","90272","10013","10007","94123","77449","11368","60629","79936","75034"]
data = []

for i, val in enumerate(zipcodes):
    response = requests.get(str(AQ_URL + val + AQ_KEY + API_KEY )).content
    airqualities = json.loads(response)
    
    details = ""
    location = ""
    
    for jsonitems in airqualities:
         print(val)
         location = 'Location {0} {1} @ {2},{3}'.format(jsonitems.get('ReportingArea','North'),  jsonitems.get('StateCode','NY'), jsonitems.get('Latitude',0),jsonitems.get('Longitude',0)  )
         details = 'Current Air Quality Reading for {0} is {1} for {2} at Hour {3} on {4}.'.format( jsonitems.get('ParameterName','O3'),jsonitems.get('AQI',0), location, jsonitems.get('HourObserved',1),jsonitems.get('DateObserved','2024-01-01'))
    
         data.append({"DateObserved": jsonitems.get('DateObserved',''), 
                      "HourObserved": jsonitems.get('HourObserved',0), 
                      "Latitude": jsonitems.get('Latitude',0), 
                      "Longitude": jsonitems.get('Longitude',0), 
                      "ParameterName": jsonitems.get('ParameterName',''), 
                      "ZipCode": str(val),
                      "AQI": jsonitems.get('AQI',0), 
                      "vector": model(details), "details": details, "location": location})
        

res = milvus_client.insert(collection_name=COLLECTION_NAME, data=data)
print(res)
#print(data)

08520
08520
94027
94027
02199
02199
02199
11962
94957
94957
90402
94301
94301
07070
07070
90265
90265
90272
10013
10013
10007
10007
94123
94123
77449
77449
11368
11368
60629
60629
79936
79936
79936
75034
75034
{'insert_count': 35, 'ids': [451727117965264698, 451727117965264699, 451727117965264700, 451727117965264701, 451727117965264702, 451727117965264703, 451727117965264704, 451727117965264705, 451727117965264706, 451727117965264707, 451727117965264708, 451727117965264709, 451727117965264710, 451727117965264711, 451727117965264712, 451727117965264713, 451727117965264714, 451727117965264715, 451727117965264716, 451727117965264717, 451727117965264718, 451727117965264719, 451727117965264720, 451727117965264721, 451727117965264722, 451727117965264723, 451727117965264724, 451727117965264725, 451727117965264726, 451727117965264727, 451727117965264728, 451727117965264729, 451727117965264730, 451727117965264731, 451727117965264732], 'cost': 15}


In [50]:


# Define search parameters
search_params = {
    "metric_type": "L2",
    "params": {"nprobe": 10}
}

# Use first record as search record
query_vector = [data[0]["vector"]]

# Execute the search on the 'vector' field
search_results = milvus_client.search(
    COLLECTION_NAME,
    data=query_vector,
    anns_field="vector",
    output_fields=["id", "DateObserved", "HourObserved", "Latitude", "Longitude", "ParameterName", "ZipCode", "AQI", "details", "location"],
    search_params=search_params,
    limit=10
)

# Print search results
for hits in search_results:
    for hit in hits:
        print(f"Hit: {hit}")



In [67]:
from datetime import datetime

details = ""
fulllocation = ""
data = []

OAQ_COLLECTION_NAME = "openaq"
OPENAQ_URI = "https://api.openaq.org/v1/measurements?country=US&date%5C_from="
TODAYS_DATE = str( datetime.today().strftime('%Y-%m-%d') ) 

## schema

schema = milvus_client.create_schema(
    enable_dynamic_field=False
)

schema.add_field(field_name='id', datatype=DataType.INT64, is_primary=True, auto_id=True)
schema.add_field(field_name='datelocal', datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name="unit", datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name="latitude", datatype=DataType.FLOAT)
schema.add_field(field_name="longitude", datatype=DataType.FLOAT)
schema.add_field(field_name="country", datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name="city", datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name='parameter', datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name="value", datatype=DataType.FLOAT)
schema.add_field(field_name="relativehumidity", datatype=DataType.FLOAT)
schema.add_field(field_name='location', datatype=DataType.VARCHAR, max_length=512)
schema.add_field(field_name="vector", datatype=DataType.FLOAT_VECTOR, dim=DIMENSION)
schema.add_field(field_name="details",  datatype=DataType.VARCHAR, max_length=8000)
schema.add_field(field_name="fulllocation",  datatype=DataType.VARCHAR, max_length=2000)

index_params = milvus_client.prepare_index_params()

index_params.add_index(
    field_name="id",
    index_type="STL_SORT"
)

index_params.add_index(
    field_name="vector",
    index_type="IVF_FLAT",
    metric_type="L2",
    params={"nlist": 100}
)

milvus_client.create_collection(
    collection_name = OAQ_COLLECTION_NAME,
    schema=schema,
    index_params=index_params
)

res = milvus_client.get_load_state(
    collection_name = OAQ_COLLECTION_NAME
)

print(res)

response = requests.get(str(OPENAQ_URI + TODAYS_DATE )).content
openaq = json.loads(response)

for jsonitems in openaq['results']:
    fulllocation = 'Location {0} {1} {2} @ {3},{4}'.format(jsonitems.get('location'),jsonitems.get('country'),jsonitems.get('city'), 
                                                           jsonitems.get('coordinates')['latitude'],jsonitems.get('coordinates')['longitude'] )
    details = 'Current Air Quality Reading for {0} is {1} {2} {3} for {4} at {5}.'.format( jsonitems.get('parameter'), jsonitems.get('value'), 
                                                                                      jsonitems.get('unit'),
                                                                                      jsonitems.get('relativehumidity'),  
                                                                                      fulllocation, jsonitems.get('date')['local'])  

    data.append({ "datelocal": str(jsonitems.get('date')['local']), 
                  "unit": str(jsonitems.get('unit','')), 
                  "latitude": float(jsonitems.get('coordinates')['latitude']), 
                  "longitude": float(jsonitems.get('coordinates')['longitude']), 
                  "country": str(jsonitems.get('country','')), 
                  "city": str(jsonitems.get('city','')), 
                  "parameter": str(jsonitems.get('parameter','')), 
                  "value": float(jsonitems.get('value')), 
                  "relativehumidity":  float(jsonitems.get('relativehumidity',0.0)), 
                  "location": str(jsonitems.get('location','')), 
                  "vector": model(details), "details": str(details), "fulllocation": str(fulllocation)})

    #print(details)
    #break

res = milvus_client.insert(collection_name=OAQ_COLLECTION_NAME, data=data)
print(res)
#print(data)


{'state': <LoadState: Loaded>}
{'insert_count': 100, 'ids': [451730705222738740, 451730705222738741, 451730705222738742, 451730705222738743, 451730705222738744, 451730705222738745, 451730705222738746, 451730705222738747, 451730705222738748, 451730705222738749, 451730705222738750, 451730705222738751, 451730705222738752, 451730705222738753, 451730705222738754, 451730705222738755, 451730705222738756, 451730705222738757, 451730705222738758, 451730705222738759, 451730705222738760, 451730705222738761, 451730705222738762, 451730705222738763, 451730705222738764, 451730705222738765, 451730705222738766, 451730705222738767, 451730705222738768, 451730705222738769, 451730705222738770, 451730705222738771, 451730705222738772, 451730705222738773, 451730705222738774, 451730705222738775, 451730705222738776, 451730705222738777, 451730705222738778, 451730705222738779, 451730705222738780, 451730705222738781, 451730705222738782, 451730705222738783, 451730705222738784, 451730705222738785, 451730705222738786,

In [68]:


# Define search parameters
search_params = {
    "metric_type": "L2",
    "params": {"nprobe": 10}
}

# Use first record as search record
query_vector = [data[0]["vector"]]

# Execute the search on the 'vector' field
search_results = milvus_client.search(
    OAQ_COLLECTION_NAME,
    data=query_vector,
    anns_field="vector",
    output_fields=["id", "unit", "country", "latitude", "longitude", "parameter","value", "city", "relativehumidity", "details", "fulllocation"],
    search_params=search_params,
    limit=5
)

# Print search results
for hits in search_results:
    for hit in hits:
        print(f"Hit: {hit}")


Hit: {'id': 451730705222738740, 'distance': 0.0, 'entity': {'fulllocation': 'Location Outdoor US None @ 37.7449525946399,-122.41666532459492', 'unit': 'µg/m³', 'latitude': 37.74495315551758, 'longitude': -122.41666412353516, 'value': 6.666666507720947, 'city': 'None', 'id': 451730705222738740, 'country': 'US', 'parameter': 'pm25', 'relativehumidity': 0.0, 'details': 'Current Air Quality Reading for pm25 is 6.666666666666667 µg/m³ None for Location Outdoor US None @ 37.7449525946399,-122.41666532459492 at 2024-08-12T14:00:00-07:00.'}}
Hit: {'id': 451730705222738683, 'distance': 0.007631063926964998, 'entity': {'fulllocation': 'Location Outdoor US None @ 37.7449525946399,-122.41666532459492', 'unit': 'µg/m³', 'latitude': 37.74495315551758, 'longitude': -122.41666412353516, 'value': 6.791666507720947, 'city': 'None', 'id': 451730705222738683, 'country': 'US', 'parameter': 'pm25', 'relativehumidity': 0.0, 'details': 'Current Air Quality Reading for pm25 is 6.791666666666667 µg/m³ None for 

In [7]:
from datetime import datetime, timedelta

# https://api.openaq.org/v3/locations?order_by=id&sort_order=asc&iso=US&limit=100&page=1
# https://api.openaq.org/v3/parameters?order_by=id&sort_order=asc&limit=1000&page=1
# https://api.openaq.org/v3/countries?order_by=id&sort_order=asc&limit=1000&page=1

OAQ3_COLLECTION_NAME = "openaqmeasurements"
TODAYS_DATE = str( datetime.today().strftime('%Y-%m-%d') ) 
YESTERDAYS_DATE = (datetime.now() - timedelta(1)).strftime('%Y-%m-%d')

details = ""
fulllocation = ""
data = []

## schema

schema = milvus_client.create_schema(
    enable_dynamic_field=False
)

schema.add_field(field_name='id', datatype=DataType.INT64, is_primary=True, auto_id=True)
schema.add_field(field_name='locationId', datatype=DataType.INT32)
schema.add_field(field_name='location', datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name='parameter', datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name="value", datatype=DataType.FLOAT)
schema.add_field(field_name='datelocal', datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name="unit", datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name="latitude", datatype=DataType.FLOAT)
schema.add_field(field_name="longitude", datatype=DataType.FLOAT)
schema.add_field(field_name="country", datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name="city", datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name="isMobile", datatype=DataType.VARCHAR, max_length=12)
schema.add_field(field_name="isAnalysis", datatype=DataType.VARCHAR, max_length=12)
schema.add_field(field_name='entity', datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name='sensorType', datatype=DataType.VARCHAR, max_length=255)
schema.add_field(field_name="vector", datatype=DataType.FLOAT_VECTOR, dim=DIMENSION)
schema.add_field(field_name="details",  datatype=DataType.VARCHAR, max_length=8000)
schema.add_field(field_name="fulllocation",  datatype=DataType.VARCHAR, max_length=2000)

index_params = milvus_client.prepare_index_params()

index_params.add_index(
    field_name="id",
    index_type="STL_SORT"
)

index_params.add_index(
    field_name="vector",
    index_type="IVF_FLAT",
    metric_type="L2",
    params={"nlist": 100}
)

milvus_client.create_collection(
    collection_name = OAQ3_COLLECTION_NAME,
    schema=schema,
    index_params=index_params
)

res = milvus_client.get_load_state(
    collection_name = OAQ3_COLLECTION_NAME
)

print(res)

# for pages in range(101):
# page = 2, ...
url =  'https://api.openaq.org/v2/measurements?country=US&date_from={0}&date_to={1}&limit=1000&page=1&offset=0&sort=desc&radius=1000&order_by=datetime'.format(str(YESTERDAYS_DATE), str(TODAYS_DATE) )
headers = {"accept": "application/json"}

response = requests.get(url, headers=headers)

# print(response.text)

openaq2 = json.loads(response.text)

for jsonitems in openaq2['results']:
    fulllocation = 'Location {0}: {1}, {2}, {3} @ {4},{5}'.format(jsonitems.get('locationId'),
                                                           jsonitems.get('location'),jsonitems.get('city'),jsonitems.get('country'), 
                                                           jsonitems.get('coordinates')['latitude'],jsonitems.get('coordinates')['longitude'] )
    details = 'Current Air Quality Reading for {0} is {1} {2} for {3} at {4}. Is Mobile: {5} Is Analysis: {6} Entity: {7} Sensor Type: {8}'.format( 
                                                                                      jsonitems.get('parameter'), jsonitems.get('value'), 
                                                                                      jsonitems.get('unit'),
                                                                                      fulllocation, jsonitems.get('date')['local'],
                                                                                      jsonitems.get('isMobile'), jsonitems.get('isAnalysis'),
                                                                                      jsonitems.get('entity'), jsonitems.get('sensorType'))  

    data.append({ "locationId": int(jsonitems.get('locationId')),
                  "location": str(jsonitems.get('location','')), 
                  "parameter": str(jsonitems.get('parameter','')), 
                  "value": float(jsonitems.get('value')), 
                  "datelocal": str(jsonitems.get('date')['local']), 
                  "unit": str(jsonitems.get('unit','')), 
                  "latitude": float(jsonitems.get('coordinates')['latitude']), 
                  "longitude": float(jsonitems.get('coordinates')['longitude']), 
                  "country": str(jsonitems.get('country','')), 
                  "city": str(jsonitems.get('city','')), 
                  "isMobile": str(jsonitems.get('isMobile','')), 
                  "isAnalysis": str(jsonitems.get('isAnalysis','')), 
                  "entity": str(jsonitems.get('entity','')), 
                  "sensorType": str(jsonitems.get('sensorType','')), 
                  "vector": model(details), "details": str(details), "fulllocation": str(fulllocation)})
    # print(details)
    # break


res = milvus_client.insert(collection_name=OAQ3_COLLECTION_NAME, data=data)
# print(res)
# print(data)


{'state': <LoadState: Loaded>}
{'insert_count': 1000, 'ids': [451730705222739842, 451730705222739843, 451730705222739844, 451730705222739845, 451730705222739846, 451730705222739847, 451730705222739848, 451730705222739849, 451730705222739850, 451730705222739851, 451730705222739852, 451730705222739853, 451730705222739854, 451730705222739855, 451730705222739856, 451730705222739857, 451730705222739858, 451730705222739859, 451730705222739860, 451730705222739861, 451730705222739862, 451730705222739863, 451730705222739864, 451730705222739865, 451730705222739866, 451730705222739867, 451730705222739868, 451730705222739869, 451730705222739870, 451730705222739871, 451730705222739872, 451730705222739873, 451730705222739874, 451730705222739875, 451730705222739876, 451730705222739877, 451730705222739878, 451730705222739879, 451730705222739880, 451730705222739881, 451730705222739882, 451730705222739883, 451730705222739884, 451730705222739885, 451730705222739886, 451730705222739887, 451730705222739888

In [8]:


# Define search parameters
search_params = {
    "metric_type": "L2",
    "params": {"nprobe": 10}
}

# Use first record as search record
query_vector = [data[0]["vector"]]

# Execute the search on the 'vector' field
search_results = milvus_client.search(
    OAQ3_COLLECTION_NAME,
    data=query_vector,
    anns_field="vector",
    output_fields=["id", "unit", "country", "latitude", "longitude", "parameter","value", "city", "details", "fulllocation"],
    search_params=search_params,
    limit=5
)

# Print search results
for hits in search_results:
    for hit in hits:
        print(f"Hit: {hit}")


Hit: {'id': 451730705222738841, 'distance': 0.0, 'entity': {'unit': 'ppm', 'country': 'US', 'longitude': -95.63580322265625, 'parameter': 'o3', 'details': 'Current Air Quality Reading for o3 is 0.06 ppm for Location 173: Houston Westhollow C, None, US @ 29.7233,-95.6358 at 2024-08-11T19:00:00-05:00. Is Mobile: False Is Analysis: None Entity: Governmental Organization Sensor Type: reference grade', 'fulllocation': 'Location 173: Houston Westhollow C, None, US @ 29.7233,-95.6358', 'id': 451730705222738841, 'latitude': 29.72330093383789, 'value': 0.05999999865889549, 'city': 'None'}}
Hit: {'id': 451730705222739842, 'distance': 0.0, 'entity': {'unit': 'ppm', 'country': 'US', 'longitude': -95.63580322265625, 'parameter': 'o3', 'details': 'Current Air Quality Reading for o3 is 0.06 ppm for Location 173: Houston Westhollow C, None, US @ 29.7233,-95.6358 at 2024-08-11T19:00:00-05:00. Is Mobile: False Is Analysis: None Entity: Governmental Organization Sensor Type: reference grade', 'fulllocati